In [1]:
from __future__ import print_function
import os
os.environ['TF_C_API_GRAPH_CONSTRUCTION']='0'

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec

# plotting
import matplotlib.pyplot as plt
import seaborn as sns
from matplotlib.lines import Line2D
%matplotlib inline

import gc

import math
from math import exp
from math import ceil


from sklearn.model_selection import StratifiedKFold, RandomizedSearchCV, train_test_split, KFold
from sklearn.metrics import mean_squared_error, roc_auc_score

from scipy.stats import norm, rankdata
from scipy.stats import randint as sp_randint
from scipy.stats import uniform as sp_uniform

import keras
from keras import regularizers
from keras.layers import Input,Dropout,BatchNormalization,Activation,Add,PReLU, LSTM
from sklearn.preprocessing import MinMaxScaler, StandardScaler
from keras.models import Sequential, Model
from keras.layers import Dense, Dropout, Activation, Reshape, Flatten, Conv2D, MaxPooling2D, Conv1D, MaxPool1D, GlobalMaxPooling1D
from keras.optimizers import SGD
from keras import backend as K
from keras.callbacks import EarlyStopping, ModelCheckpoint, TensorBoard, LearningRateScheduler

import edward as ed

# module loading settings
%load_ext autoreload
%autoreload 2

import tensorflow as tf

Using TensorFlow backend.
/home/wopr/.local/lib/python3.6/site-packages/dask/config.py:168: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  data = yaml.load(f.read()) or {}


In [6]:
train = pd.read_csv('../input/train.csv')
test = pd.read_csv('../input/test.csv')
features = [f for f in train if f not in ['ID_code','target']]

In [7]:
for var in features:
    print(var)
    data = pd.concat([train[['ID_code', var]], test[['ID_code', var]]])
    train['weight_' + var] = train.groupby([var])[var].transform('count')
    test['weight_' + var] = test.groupby([var])[var].transform('count')
    train['binary_' + var] = train['weight_' + var].apply(lambda x: 1 if x > 1 else 0) * train[var]
    test['binary_' + var] = test['weight_' + var].apply(lambda x: 1 if x > 1 else 0) * test[var]

var_0
var_1
var_2
var_3
var_4
var_5
var_6
var_7
var_8
var_9
var_10
var_11
var_12
var_13
var_14
var_15
var_16
var_17
var_18
var_19
var_20
var_21
var_22
var_23
var_24
var_25
var_26
var_27
var_28
var_29
var_30
var_31
var_32
var_33
var_34
var_35
var_36
var_37
var_38
var_39
var_40
var_41
var_42
var_43
var_44
var_45
var_46
var_47
var_48
var_49
var_50
var_51
var_52
var_53
var_54
var_55
var_56
var_57
var_58
var_59
var_60
var_61
var_62
var_63
var_64
var_65
var_66
var_67
var_68
var_69
var_70
var_71
var_72
var_73
var_74
var_75
var_76
var_77
var_78
var_79
var_80
var_81
var_82
var_83
var_84
var_85
var_86
var_87
var_88
var_89
var_90
var_91
var_92
var_93
var_94
var_95
var_96
var_97
var_98
var_99
var_100
var_101
var_102
var_103
var_104
var_105
var_106
var_107
var_108
var_109
var_110
var_111
var_112
var_113
var_114
var_115
var_116
var_117
var_118
var_119
var_120
var_121
var_122
var_123
var_124
var_125
var_126
var_127
var_128
var_129
var_130
var_131
var_132
var_133
var_134
var_135
var_136
var_137
var_13

In [8]:
batch_size = 32

In [9]:
features = [f for f in train if f not in ['ID_code','target']]
df = pd.concat([train, test],axis=0,sort=False)
target = df['target']
ID = df['ID_code']
df = df[features]
train = train.reset_index(drop=True)
test = test.reset_index(drop=True)
#del train, test
#gc.collect

In [10]:
def Hbeta(D, beta):
    P = np.exp(-D * beta)
    sumP = np.sum(P)
    H = np.log(sumP) + beta * np.sum(np.multiply(D, P)) / sumP
    P = P / sumP
    return H, P

def x2p(X, u=15, tol=1e-4, print_iter=500, max_tries=50, verbose=0):
    # Initialize some variables
    n = X.shape[0]                     # number of instances
    P = np.zeros((n, n))               # empty probability matrix
    beta = np.ones(n)                  # empty precision vector
    logU = np.log(u)                   # log of perplexity (= entropy)
    
    # Compute pairwise distances
    if verbose > 0: print('Computing pairwise distances...')
    sum_X = np.sum(np.square(X), axis=1)
    # note: translating sum_X' from matlab to numpy means using reshape to add a dimension
    D = sum_X + sum_X[:,None] + -2 * X.dot(X.T)

    # Run over all datapoints
    if verbose > 0: print('Computing P-values...')
    for i in range(n):
        
        if verbose > 1 and print_iter and i % print_iter == 0:
            print('Computed P-values {} of {} datapoints...'.format(i, n))
        
        # Set minimum and maximum values for precision
        betamin = float('-inf')
        betamax = float('+inf')
        
        # Compute the Gaussian kernel and entropy for the current precision
        indices = np.concatenate((np.arange(0, i), np.arange(i + 1, n)))
        Di = D[i, indices]
        H, thisP = Hbeta(Di, beta[i])
        
        # Evaluate whether the perplexity is within tolerance
        Hdiff = H - logU
        tries = 0
        while abs(Hdiff) > tol and tries < max_tries:
            
            # If not, increase or decrease precision
            if Hdiff > 0:
                betamin = beta[i]
                if np.isinf(betamax):
                    beta[i] *= 2
                else:
                    beta[i] = (beta[i] + betamax) / 2
            else:
                betamax = beta[i]
                if np.isinf(betamin):
                    beta[i] /= 2
                else:
                    beta[i] = (beta[i] + betamin) / 2
            
            # Recompute the values
            H, thisP = Hbeta(Di, beta[i])
            Hdiff = H - logU
            tries += 1
        
        # Set the final row of P
        P[i, indices] = thisP
        
    if verbose > 0: 
        print('Mean value of sigma: {}'.format(np.mean(np.sqrt(1 / beta))))
        print('Minimum value of sigma: {}'.format(np.min(np.sqrt(1 / beta))))
        print('Maximum value of sigma: {}'.format(np.max(np.sqrt(1 / beta))))
    
    return P, beta

def compute_joint_probabilities(samples, batch_size=5000, d=2, perplexity=30, tol=1e-5, verbose=0):
    v = d - 1
    
    # Initialize some variables
    n = samples.shape[0]
    batch_size = min(batch_size, n)
    
    # Precompute joint probabilities for all batches
    if verbose > 0: print('Precomputing P-values...')
    batch_count = int(n / batch_size)
    P = np.zeros((batch_count, batch_size, batch_size))
    for i, start in enumerate(range(0, n - batch_size + 1, batch_size)):   
        curX = samples[start:start+batch_size]                   # select batch
        P[i], beta = x2p(curX, perplexity, tol, verbose=verbose) # compute affinities using fixed perplexity
        P[i][np.isnan(P[i])] = 0                                 # make sure we don't have NaN's
        P[i] = (P[i] + P[i].T) # / 2                             # make symmetric
        P[i] = P[i] / P[i].sum()                                 # obtain estimation of joint probabilities
        P[i] = np.maximum(P[i], np.finfo(P[i].dtype).eps)

    return P

In [11]:
#%time P = compute_joint_probabilities(train.values, batch_size=64, verbose=2)
#Y_train = P.reshape(train.shape[0], -1)

In [12]:
# P is the joint probabilities for this batch (Keras loss functions call this y_true)
# activations is the low-dimensional output (Keras loss functions call this y_pred)
def tsne(P, activations):
#     d = K.shape(activations)[1]
    d = 2 # TODO: should set this automatically, but the above is very slow for some reason
    n = batch_size # TODO: should set this automatically
    v = d - 1.
    eps = K.variable(10e-15) # needs to be at least 10e-8 to get anything after Q /= K.sum(Q)
    sum_act = K.sum(K.square(activations), axis=1)
    Q = K.reshape(sum_act, [-1, 1]) + -2 * K.dot(activations, K.transpose(activations))
    Q = (sum_act + Q) / v
    Q = K.pow(1 + Q, -(v + 1) / 2)
    Q *= K.variable(1 - np.eye(n))
    Q /= K.sum(Q)
    Q = K.maximum(Q, eps)
    C = K.log((P + eps) / (Q + eps))
    C = K.sum(P * C)
    return C

In [13]:
#model = Sequential()
#model.add(Dense(500, activation='relu', input_shape=(train.shape[1],)))
#model.add(Dense(500, activation='relu'))
#model.add(Dense(2000, activation='relu'))
#model.add(Dense(2))
#model.summary()
#sgd = SGD(lr=0.1)
#%time model.compile(loss=tsne, optimizer='adam')

In [14]:
#%time model.fit(train.values, Y_train, batch_size=batch_size, shuffle=False, nb_epoch=2)

In [15]:
#Y_train = P.reshape(train.shape[0], -1)

In [16]:
#print(train.shape)
#print(Y_train.shape)

In [ ]:
def plot_model(embedding, labels):
    fig = plt.figure(figsize=(8,8))
    plt.scatter(embedding[:,0], embedding[:,1], marker='o', s=1, edgecolor='', c=labels)
    fig.tight_layout()
    
from matplotlib.lines import Line2D
def plot_differences(embedding, actual, lim=1000):
    fig = plt.figure(figsize=(8,8))
    ax = fig.gca()
    for a, b in zip(embedding, actual)[:lim]:
        ax.add_line(Line2D((a[0], b[0]), (a[1], b[1]), linewidth=1))
    ax.autoscale_view()
    plt.show()
plot_model(model.predict(train[group7].values), target)

In [17]:
group1=['var_12','var_13','var_108','var_126','var_68']
group2=['var_23','var_35','var_52', 'var_67', 'var_118', 'var_169', 'var_172', 'var_173']
group3=['var_0','var_2','var_6', 'var_26', 'var_44', 'var_76', 'var_80', 'var_86',
        'var_106','var_110', 'var_111', 'var_123', 'var_155', 'var_157',
        'var_162','var_174', 'var_181', 'var_198']
group4=['var_1','var_5','var_15', 'var_24', 'var_34', 'var_49', 'var_53', 'var_94',
        'var_109','var_122', 'var_127', 'var_137', 'var_145', 'var_165',
        'var_166','var_171', 'var_180']
group5=['var_3', 'var_154']
group6=['var_4','var_35','var_173', 'var_198']
group7=['var_9','var_12','var_55', 'var_75', 'var_79', 'var_83', 'var_94', 'var_95',
        'var_99','var_113', 'var_114', 'var_122', 'var_131', 'var_141',
        'var_154','var_165']

group_list = [group1, group2, group3, group4, group5, group6, group7]
i = 0

In [19]:
for group in group_list:
    i += 1
    print(group)
    
    model = Sequential()
    model.add(Dense(500, activation='relu', input_shape=(train[group].shape[1],)))
    model.add(Dense(500, activation='relu'))
    model.add(Dense(2000, activation='relu'))
    model.add(Dense(2))
    model.summary()
    sgd = SGD(lr=0.1)
    %time model.compile(loss=tsne, optimizer='adam')
    
    P = compute_joint_probabilities(train[group].values, batch_size=batch_size, verbose=0)
    Y_train = P.reshape(train[group].shape[0], -1)
    model.fit(train[group].values, Y_train, batch_size=batch_size, shuffle=False, nb_epoch=6)
    
    a = pd.DataFrame(model.predict(df[group].values))
    a = a.reset_index(drop=True)
    df = df.reset_index(drop=True)
    
    df = pd.concat([df, a], axis=1)
    df = df.rename(index=str, columns={0: "tsne_0_" + "group_" + str(i), 1: "tsne_1_" + "group_" + str(i)})

['var_12', 'var_13', 'var_108', 'var_126', 'var_68']
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_5 (Dense)              (None, 500)               3000      
_________________________________________________________________
dense_6 (Dense)              (None, 500)               250500    
_________________________________________________________________
dense_7 (Dense)              (None, 2000)              1002000   
_________________________________________________________________
dense_8 (Dense)              (None, 2)                 4002      
Total params: 1,259,502
Trainable params: 1,259,502
Non-trainable params: 0
_________________________________________________________________
CPU times: user 26.2 ms, sys: 0 ns, total: 26.2 ms
Wall time: 26 ms
Instructions for updating:
Use tf.cast instead.


/home/wopr/.local/lib/python3.6/site-packages/ipykernel_launcher.py:16: UserWarning: The `nb_epoch` argument in `fit` has been renamed `epochs`.
  app.launch_new_instance()


Epoch 1/6
200000/200000 [==============================] - 29s 147us/step - loss: 0.0012
Epoch 2/6
200000/200000 [==============================] - 26s 130us/step - loss: 8.4885e-04
Epoch 3/6
200000/200000 [==============================] - 26s 130us/step - loss: 8.0597e-04
Epoch 4/6
200000/200000 [==============================] - 26s 129us/step - loss: 7.8093e-04
Epoch 5/6
200000/200000 [==============================] - 26s 128us/step - loss: 7.6943e-04
Epoch 6/6
200000/200000 [==============================] - 25s 127us/step - loss: 7.6284e-04
['var_23', 'var_35', 'var_52', 'var_67', 'var_118', 'var_169', 'var_172', 'var_173']
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_9 (Dense)              (None, 500)               4500      
_________________________________________________________________
dense_10 (Dense)             (None, 500)               250500    
_______________________________

/home/wopr/.local/lib/python3.6/site-packages/ipykernel_launcher.py:4: RuntimeWarning: divide by zero encountered in log
  after removing the cwd from sys.path.
/home/wopr/.local/lib/python3.6/site-packages/ipykernel_launcher.py:4: RuntimeWarning: invalid value encountered in double_scalars
  after removing the cwd from sys.path.
/home/wopr/.local/lib/python3.6/site-packages/ipykernel_launcher.py:5: RuntimeWarning: invalid value encountered in true_divide
  """
/home/wopr/.local/lib/python3.6/site-packages/ipykernel_launcher.py:16: UserWarning: The `nb_epoch` argument in `fit` has been renamed `epochs`.
  app.launch_new_instance()


Epoch 1/6
200000/200000 [==============================] - 26s 131us/step - loss: 0.0109
Epoch 2/6
200000/200000 [==============================] - 26s 130us/step - loss: 0.0103
Epoch 3/6
200000/200000 [==============================] - 26s 131us/step - loss: 0.0103
Epoch 4/6
200000/200000 [==============================] - 26s 130us/step - loss: 0.0103
Epoch 5/6
200000/200000 [==============================] - 26s 130us/step - loss: 0.0102
Epoch 6/6
200000/200000 [==============================] - 26s 130us/step - loss: 0.0102
['var_0', 'var_2', 'var_6', 'var_26', 'var_44', 'var_76', 'var_80', 'var_86', 'var_106', 'var_110', 'var_111', 'var_123', 'var_155', 'var_157', 'var_162', 'var_174', 'var_181', 'var_198']
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_13 (Dense)             (None, 500)               9500      
_________________________________________________________________
dense_14 (Dens

...

Epoch 1/6
200000/200000 [==============================] - 27s 134us/step - loss: 0.0014
Epoch 2/6
200000/200000 [==============================] - 26s 132us/step - loss: 0.0012
Epoch 3/6
200000/200000 [==============================] - 26s 132us/step - loss: 0.0011
Epoch 4/6
200000/200000 [==============================] - 26s 132us/step - loss: 0.0011
Epoch 5/6
200000/200000 [==============================] - 26s 132us/step - loss: 0.0011
Epoch 6/6
200000/200000 [==============================] - 26s 132us/step - loss: 0.0011
['var_4', 'var_35', 'var_173', 'var_198']
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_25 (Dense)             (None, 500)               2500      
_________________________________________________________________
dense_26 (Dense)             (None, 500)               250500    
_________________________________________________________________
dense_27 (Dense)            

/home/wopr/.local/lib/python3.6/site-packages/ipykernel_launcher.py:16: UserWarning: The `nb_epoch` argument in `fit` has been renamed `epochs`.
  app.launch_new_instance()


Epoch 1/6
200000/200000 [==============================] - 26s 132us/step - loss: 0.0033
Epoch 2/6
200000/200000 [==============================] - 26s 130us/step - loss: 0.0030
Epoch 3/6
200000/200000 [==============================] - 26s 130us/step - loss: 0.0029
Epoch 4/6
200000/200000 [==============================] - 26s 130us/step - loss: 0.0029
Epoch 5/6
200000/200000 [==============================] - 26s 130us/step - loss: 0.0029
Epoch 6/6
200000/200000 [==============================] - 26s 131us/step - loss: 0.0029
['var_9', 'var_12', 'var_55', 'var_75', 'var_79', 'var_83', 'var_94', 'var_95', 'var_99', 'var_113', 'var_114', 'var_122', 'var_131', 'var_141', 'var_154', 'var_165']
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_29 (Dense)             (None, 500)               8500      
_________________________________________________________________
dense_30 (Dense)             (None,

/home/wopr/.local/lib/python3.6/site-packages/ipykernel_launcher.py:16: UserWarning: The `nb_epoch` argument in `fit` has been renamed `epochs`.
  app.launch_new_instance()


Epoch 1/6
200000/200000 [==============================] - 27s 135us/step - loss: 0.0137
Epoch 2/6
200000/200000 [==============================] - 27s 135us/step - loss: 0.0131
Epoch 3/6
200000/200000 [==============================] - 27s 133us/step - loss: 0.0130
Epoch 4/6
200000/200000 [==============================] - 27s 136us/step - loss: 0.0130
Epoch 5/6
200000/200000 [==============================] - 27s 133us/step - loss: 0.0130
Epoch 6/6
200000/200000 [==============================] - 27s 134us/step - loss: 0.0129


In [24]:
for feature in df.filter(like='tsne').columns:
    df['mean_'+feature] = (df[feature].mean()-df[feature])
    df['zscore_'+feature] = (df[feature] - df[feature].mean())/df[feature].std(ddof=0)
    df['sq_'+feature] = (df[feature])**2
    df['sqrt_'+feature] = np.abs(df[feature])**(1/2)
    df['cp_'+feature] = pd.DataFrame(rankdata(df[feature]))
    df['cnp_'+feature] = pd.DataFrame((norm.cdf(df[feature])))
#    df['zscorecountarctan'+feature]=(np.arctan(df['weight_'+features])2/np.pi)df['zscore_'+feature]
#    df['zscorecount' +feature] = df['zscore_'+feature] * ((df['weight_'+feature]-df['weight_'+feature].min())/((df['weight_'+feature].max()-df['weight_'+feature].min())*8+1))
    
    

/home/wopr/.local/lib/python3.6/site-packages/scipy/stats/_distn_infrastructure.py:877: RuntimeWarning: invalid value encountered in greater
  return (self.a < x) & (x < self.b)
/home/wopr/.local/lib/python3.6/site-packages/scipy/stats/_distn_infrastructure.py:877: RuntimeWarning: invalid value encountered in less
  return (self.a < x) & (x < self.b)
/home/wopr/.local/lib/python3.6/site-packages/scipy/stats/_distn_infrastructure.py:1748: RuntimeWarning: invalid value encountered in greater_equal
  cond2 = (x >= self.b) & cond0


In [25]:
for df in [df]:
#####Handling Missing Values#####     
    for i in range(len(df.columns)):
        df.iloc[:,i] = (df.iloc[:,i]).fillna(-1)

In [26]:
df['target'] = target.values
df['ID_code'] = id
features = [f for f in df if f not in ['ID_code','target']]

train = df[df['target'].notnull()]
test = df[df['target'].isnull()]

print(df.shape)
print(train.shape)
print(test.shape)
print(df.head(5))
print(train.head(5))

(400000, 736)
(200000, 736)
(200000, 736)
     var_0   var_1    var_2   var_3    var_4   var_5   var_6    var_7   var_8  \
0   8.9255 -6.7863  11.9081  5.0930  11.4607 -9.2834  5.1187  18.6266 -4.9200   
1  11.5006 -4.1473  13.8588  5.3890  12.3622  7.0433  5.6208  16.5338  3.1468   
2   8.6093 -2.7457  12.0805  7.8928  10.5825 -9.0837  6.9427  14.6155 -4.9193   
3  11.0604 -2.1518   8.9522  7.1957  12.5846 -1.8361  5.8428  14.9250 -5.8609   
4   9.8369 -1.4834  12.8746  6.6375  12.2772  2.4486  5.9405  19.2514  6.2654   

    var_9  ...  sq_cp_tsne_0_group_2  sqrt_cp_tsne_0_group_2  \
0  5.7470  ...                  -1.0                    -1.0   
1  8.0851  ...                  -1.0                    -1.0   
2  5.9525  ...                  -1.0                    -1.0   
3  8.2450  ...                  -1.0                    -1.0   
4  7.6784  ...                  -1.0                    -1.0   

   cp_cp_tsne_0_group_2  cnp_cp_tsne_0_group_2  mean_cnp_tsne_0_group_2  \
0          

In [27]:
# define roc_callback, inspired by https://github.com/keras-team/keras/issues/6050#issuecomment-329996505
def auc_roc(y_true, y_pred):
    # any tensorflow metric
    value, update_op = tf.contrib.metrics.streaming_auc(y_pred, y_true)

    # find all variables created for this metric
    metric_vars = [i for i in tf.local_variables() if 'auc_roc' in i.name.split('/')[1]]

    # Add metric variables to GLOBAL_VARIABLES collection.
    # They will be initialized for new session.
    for v in metric_vars:
        tf.add_to_collection(tf.GraphKeys.GLOBAL_VARIABLES, v)

    # force to update metric values
    with tf.control_dependencies([update_op]):
        value = tf.identity(value)
        return value

In [28]:
NUM_GPUS=2
learning_rate = 0.001
nb_epoch = int(100)
dcy = learning_rate / nb_epoch

nb_folds = 5
runs_per_fold = 3 #bagging on each fold
cv_roc = []

oof = np.zeros(shape=(np.shape(train)[0], 1))
predict = np.zeros(shape=(np.shape(test)[0], 1))

In [29]:
def augment(x,y,t=2):
    xs,xn = [],[]
    for i in range(t):
        mask = y>0
        x1 = x[mask].copy()
        ids = np.arange(x1.shape[0])
        for c in range(x1.shape[1]):
            np.random.shuffle(ids)
            x1[:,c] = x1[ids][:,c]
        xs.append(x1)

    for i in range(t//2):
        mask = y==0
        x1 = x[mask].copy()
        ids = np.arange(x1.shape[0])
        for c in range(x1.shape[1]):
            np.random.shuffle(ids)
            x1[:,c] = x1[ids][:,c]
        xn.append(x1)

    xs = np.vstack(xs)
    xn = np.vstack(xn)
    ys = np.ones(xs.shape[0])
    yn = np.zeros(xn.shape[0])
    x = np.vstack([x,xs,xn])
    y = np.concatenate([y,ys,yn])
    return x,y

In [ ]:
import lightgbm as lgb
folds = KFold(n_splits = nb_folds, random_state = 80085, shuffle = True)
for fold_, (trn_idx, val_idx) in enumerate(folds.split(train)):
    print("fold {}".format(fold_))

    train_x, train_y = train[features].iloc[trn_idx], train['target'].iloc[trn_idx]
    valid_x, valid_y = train[features].iloc[val_idx], train['target'].iloc[val_idx]

    #columns = ['var_12', 'var_75', 'var_81', 'var_83', 'var_89',
    #           'var_95', 'var_99', 'var_113', 'var_122', 'var_139', 'var_154', 'var_190']
    #for var in train_x[columns]:
    #    print(var)
    #    hist, bin_edges = np.histogram(train_x[var], density=True)
    #    train_x['test_' + var] = [hist[np.searchsorted(bin_edges,ele)-1] for ele in train_x[var]]
    #for var in valid_x[columns]:
    #    print(var)
    #    hist, bin_edges = np.histogram(valid_x[var], density=True)
    #    valid_x['test_' + var] = [hist[np.searchsorted(bin_edges,ele)-1] for ele in valid_x[var]]


    train_x, train_y = augment(train_x.values, train_y.values)
    train_x = pd.DataFrame(train_x)
    train_y = pd.DataFrame(train_y)

    #track oof bagged prediction for cv scores
    oof = 0
    for j in range(runs_per_fold):
        lgb_train = lgb.Dataset(train_x,
                                label=train_y,
                                free_raw_data=False)
        lgb_test = lgb.Dataset(valid_x,
                               label=valid_y,
                               free_raw_data=False)

        # params optimized by optuna
        params ={
            "objective" : "binary",
            "metric" : "auc",
            "boosting": 'gbdt',
            "max_depth" : -1,
            "num_leaves" : 31,
            "learning_rate" : 0.01,
            "bagging_freq": 5,
            "bagging_fraction" : 0.4,
            "feature_fraction" : 0.05,
            "min_data_in_leaf": 150,
            "min_sum_heassian_in_leaf": 10,
            "tree_learner": "serial",
            "boost_from_average": "false",
            "bagging_seed" : 80085,
            "verbosity" : 1,
            'device' : 'gpu'
            } 

        reg = lgb.train(
                        params,
                        lgb_train,
                        valid_sets=[lgb_train, lgb_test],
                        valid_names=['train', 'valid'],
                        num_boost_round=60000,
                        verbose_eval=1,
                        early_stopping_rounds=3000
                        )

        val_roc = roc_auc_score(valid_y, reg.predict(valid_x))   
        print ('\nFold %d Run %d Results *****' % (fold_, j))
        print ('Validation ROC: %.5f\n' % (val_roc))
        curr_pred = reg.predict(test[features]) / runs_per_fold
        oof += pd.DataFrame(curr_pred)
        cv_roc.append(val_roc)
        print ('\nFold %d prediction cv roc: %.5f\n' % (fold_, val_roc))
    predict += oof / nb_folds    
    print('Mean out of fold roc: %.5f' % np.mean(cv_roc))

predictions = pd.DataFrame(predict)

fold 0
[1]	train's auc: 0.621053	valid's auc: 0.614155
Training until validation scores don't improve for 3000 rounds.
[2]	train's auc: 0.68016	valid's auc: 0.658335
[3]	train's auc: 0.702396	valid's auc: 0.676085
[4]	train's auc: 0.720954	valid's auc: 0.691459
[5]	train's auc: 0.74187	valid's auc: 0.716178
[6]	train's auc: 0.760304	valid's auc: 0.729016
[7]	train's auc: 0.768749	valid's auc: 0.735305
[8]	train's auc: 0.79038	valid's auc: 0.747585
[9]	train's auc: 0.799905	valid's auc: 0.754898
[10]	train's auc: 0.810899	valid's auc: 0.76354
[11]	train's auc: 0.817083	valid's auc: 0.764337
[12]	train's auc: 0.824738	valid's auc: 0.770162
[13]	train's auc: 0.830029	valid's auc: 0.776078
[14]	train's auc: 0.832119	valid's auc: 0.77971
[15]	train's auc: 0.838316	valid's auc: 0.783727
[16]	train's auc: 0.841171	valid's auc: 0.783243
[17]	train's auc: 0.849929	valid's auc: 0.789612
[18]	train's auc: 0.853033	valid's auc: 0.791983
[19]	train's auc: 0.853746	valid's auc: 0.791542
[20]	train's

[167]	train's auc: 0.906924	valid's auc: 0.829964
[168]	train's auc: 0.907188	valid's auc: 0.830462
[169]	train's auc: 0.907434	valid's auc: 0.830719
[170]	train's auc: 0.907538	valid's auc: 0.830844
[171]	train's auc: 0.907446	valid's auc: 0.830478
[172]	train's auc: 0.907202	valid's auc: 0.8302
[173]	train's auc: 0.907585	valid's auc: 0.830746
[174]	train's auc: 0.907973	valid's auc: 0.831445
[175]	train's auc: 0.907976	valid's auc: 0.831304
[176]	train's auc: 0.908057	valid's auc: 0.831488
[177]	train's auc: 0.908085	valid's auc: 0.831499
[178]	train's auc: 0.908214	valid's auc: 0.831729
[179]	train's auc: 0.908373	valid's auc: 0.831996
[180]	train's auc: 0.908584	valid's auc: 0.832397
[181]	train's auc: 0.908644	valid's auc: 0.83256
[182]	train's auc: 0.908694	valid's auc: 0.832935
[183]	train's auc: 0.908707	valid's auc: 0.832774
[184]	train's auc: 0.908892	valid's auc: 0.83327
[185]	train's auc: 0.908992	valid's auc: 0.833402
[186]	train's auc: 0.909066	valid's auc: 0.833617
[187

[333]	train's auc: 0.918693	valid's auc: 0.844587
[334]	train's auc: 0.918656	valid's auc: 0.844579
[335]	train's auc: 0.918861	valid's auc: 0.844802
[336]	train's auc: 0.918983	valid's auc: 0.84495
[337]	train's auc: 0.919181	valid's auc: 0.845093
[338]	train's auc: 0.919246	valid's auc: 0.845129
[339]	train's auc: 0.919254	valid's auc: 0.845173
[340]	train's auc: 0.919302	valid's auc: 0.845176
[341]	train's auc: 0.919431	valid's auc: 0.845281
[342]	train's auc: 0.919525	valid's auc: 0.845409
[343]	train's auc: 0.919624	valid's auc: 0.845605
[344]	train's auc: 0.919444	valid's auc: 0.845313
[345]	train's auc: 0.919449	valid's auc: 0.845221
[346]	train's auc: 0.919503	valid's auc: 0.845305
[347]	train's auc: 0.919612	valid's auc: 0.845455
[348]	train's auc: 0.919768	valid's auc: 0.845726
[349]	train's auc: 0.919664	valid's auc: 0.84557
[350]	train's auc: 0.919698	valid's auc: 0.845556
[351]	train's auc: 0.919704	valid's auc: 0.845624
[352]	train's auc: 0.919737	valid's auc: 0.845719
[3

[499]	train's auc: 0.924935	valid's auc: 0.852662
[500]	train's auc: 0.924847	valid's auc: 0.852579
[501]	train's auc: 0.924921	valid's auc: 0.852674
[502]	train's auc: 0.925005	valid's auc: 0.852757
[503]	train's auc: 0.925081	valid's auc: 0.852779
[504]	train's auc: 0.925097	valid's auc: 0.85278
[505]	train's auc: 0.925163	valid's auc: 0.852922
[506]	train's auc: 0.925164	valid's auc: 0.852928
[507]	train's auc: 0.925211	valid's auc: 0.852983
[508]	train's auc: 0.925186	valid's auc: 0.85298
[509]	train's auc: 0.925293	valid's auc: 0.85308
[510]	train's auc: 0.925333	valid's auc: 0.853124
[511]	train's auc: 0.925404	valid's auc: 0.853273
[512]	train's auc: 0.925362	valid's auc: 0.853227
[513]	train's auc: 0.925348	valid's auc: 0.853184
[514]	train's auc: 0.925411	valid's auc: 0.853286
[515]	train's auc: 0.925439	valid's auc: 0.853246
[516]	train's auc: 0.925532	valid's auc: 0.853359
[517]	train's auc: 0.925621	valid's auc: 0.853496
[518]	train's auc: 0.925611	valid's auc: 0.853397
[51

[665]	train's auc: 0.930681	valid's auc: 0.860012
[666]	train's auc: 0.930727	valid's auc: 0.860106
[667]	train's auc: 0.930764	valid's auc: 0.860168
[668]	train's auc: 0.930808	valid's auc: 0.860208
[669]	train's auc: 0.930847	valid's auc: 0.860261
[670]	train's auc: 0.930849	valid's auc: 0.860289
[671]	train's auc: 0.930875	valid's auc: 0.860333
[672]	train's auc: 0.930902	valid's auc: 0.860375
[673]	train's auc: 0.930958	valid's auc: 0.860467
[674]	train's auc: 0.930992	valid's auc: 0.860541
[675]	train's auc: 0.931032	valid's auc: 0.860576
[676]	train's auc: 0.931065	valid's auc: 0.860628
[677]	train's auc: 0.931093	valid's auc: 0.860651
[678]	train's auc: 0.931083	valid's auc: 0.860627
[679]	train's auc: 0.93113	valid's auc: 0.860664
[680]	train's auc: 0.931153	valid's auc: 0.860661
[681]	train's auc: 0.931183	valid's auc: 0.860674
[682]	train's auc: 0.931168	valid's auc: 0.860644
[683]	train's auc: 0.931184	valid's auc: 0.860708
[684]	train's auc: 0.931197	valid's auc: 0.860708
[

...

[22064]	train's auc: 0.997763	valid's auc: 0.909524
[22065]	train's auc: 0.997764	valid's auc: 0.909527
[22066]	train's auc: 0.997764	valid's auc: 0.909527
[22067]	train's auc: 0.997765	valid's auc: 0.909523
[22068]	train's auc: 0.997765	valid's auc: 0.90952
[22069]	train's auc: 0.997765	valid's auc: 0.909518
[22070]	train's auc: 0.997766	valid's auc: 0.909516
[22071]	train's auc: 0.997766	valid's auc: 0.909515
[22072]	train's auc: 0.997766	valid's auc: 0.909515
[22073]	train's auc: 0.997767	valid's auc: 0.909513
[22074]	train's auc: 0.997767	valid's auc: 0.909513
[22075]	train's auc: 0.997768	valid's auc: 0.909513
[22076]	train's auc: 0.997768	valid's auc: 0.909514
[22077]	train's auc: 0.997769	valid's auc: 0.909515
[22078]	train's auc: 0.997769	valid's auc: 0.909515
[22079]	train's auc: 0.997769	valid's auc: 0.909516
[22080]	train's auc: 0.99777	valid's auc: 0.909516
[22081]	train's auc: 0.99777	valid's auc: 0.909513
[22082]	train's auc: 0.997771	valid's auc: 0.909513
[22083]	train's

[22224]	train's auc: 0.997834	valid's auc: 0.909479
[22225]	train's auc: 0.997834	valid's auc: 0.909479
[22226]	train's auc: 0.997834	valid's auc: 0.909481
[22227]	train's auc: 0.997835	valid's auc: 0.90948
[22228]	train's auc: 0.997835	valid's auc: 0.909482
[22229]	train's auc: 0.997835	valid's auc: 0.909484
[22230]	train's auc: 0.997836	valid's auc: 0.909481
[22231]	train's auc: 0.997836	valid's auc: 0.909483
[22232]	train's auc: 0.997837	valid's auc: 0.909483
[22233]	train's auc: 0.997837	valid's auc: 0.909483
[22234]	train's auc: 0.997837	valid's auc: 0.909481
[22235]	train's auc: 0.997838	valid's auc: 0.90948
[22236]	train's auc: 0.997838	valid's auc: 0.90948
[22237]	train's auc: 0.997839	valid's auc: 0.909483
[22238]	train's auc: 0.997839	valid's auc: 0.909482
[22239]	train's auc: 0.997839	valid's auc: 0.909481
[22240]	train's auc: 0.99784	valid's auc: 0.90948
[22241]	train's auc: 0.99784	valid's auc: 0.909479
[22242]	train's auc: 0.997841	valid's auc: 0.909479
[22243]	train's au

[22385]	train's auc: 0.997903	valid's auc: 0.909471
[22386]	train's auc: 0.997903	valid's auc: 0.909473
[22387]	train's auc: 0.997904	valid's auc: 0.909473
[22388]	train's auc: 0.997904	valid's auc: 0.909473
[22389]	train's auc: 0.997905	valid's auc: 0.909473
[22390]	train's auc: 0.997905	valid's auc: 0.909473
[22391]	train's auc: 0.997905	valid's auc: 0.909471
[22392]	train's auc: 0.997906	valid's auc: 0.909472
[22393]	train's auc: 0.997907	valid's auc: 0.909473
[22394]	train's auc: 0.997907	valid's auc: 0.909472
[22395]	train's auc: 0.997907	valid's auc: 0.909473
[22396]	train's auc: 0.997908	valid's auc: 0.909473
[22397]	train's auc: 0.997909	valid's auc: 0.909474
[22398]	train's auc: 0.997909	valid's auc: 0.909475
[22399]	train's auc: 0.997909	valid's auc: 0.909475
[22400]	train's auc: 0.99791	valid's auc: 0.909476
[22401]	train's auc: 0.99791	valid's auc: 0.909477
[22402]	train's auc: 0.997911	valid's auc: 0.909478
[22403]	train's auc: 0.997912	valid's auc: 0.909476
[22404]	train'

[22544]	train's auc: 0.997975	valid's auc: 0.909483
[22545]	train's auc: 0.997975	valid's auc: 0.909481
[22546]	train's auc: 0.997975	valid's auc: 0.909478
[22547]	train's auc: 0.997976	valid's auc: 0.909478
[22548]	train's auc: 0.997976	valid's auc: 0.909477
[22549]	train's auc: 0.997976	valid's auc: 0.909477
[22550]	train's auc: 0.997977	valid's auc: 0.909476
[22551]	train's auc: 0.997977	valid's auc: 0.909476
[22552]	train's auc: 0.997978	valid's auc: 0.909476
[22553]	train's auc: 0.997978	valid's auc: 0.909478
[22554]	train's auc: 0.997978	valid's auc: 0.909479
[22555]	train's auc: 0.997979	valid's auc: 0.90948
[22556]	train's auc: 0.997979	valid's auc: 0.909481
[22557]	train's auc: 0.997979	valid's auc: 0.909482
[22558]	train's auc: 0.99798	valid's auc: 0.909482
[22559]	train's auc: 0.99798	valid's auc: 0.90948
[22560]	train's auc: 0.997981	valid's auc: 0.909481
[22561]	train's auc: 0.997981	valid's auc: 0.90948
[22562]	train's auc: 0.997981	valid's auc: 0.909481
[22563]	train's a

[22704]	train's auc: 0.998046	valid's auc: 0.90948
[22705]	train's auc: 0.998046	valid's auc: 0.909479
[22706]	train's auc: 0.998046	valid's auc: 0.909482
[22707]	train's auc: 0.998047	valid's auc: 0.909483
[22708]	train's auc: 0.998047	valid's auc: 0.909484
[22709]	train's auc: 0.998048	valid's auc: 0.909483
[22710]	train's auc: 0.998048	valid's auc: 0.909483
[22711]	train's auc: 0.998049	valid's auc: 0.909485
[22712]	train's auc: 0.998049	valid's auc: 0.909484
[22713]	train's auc: 0.998049	valid's auc: 0.909485
[22714]	train's auc: 0.99805	valid's auc: 0.909481
[22715]	train's auc: 0.99805	valid's auc: 0.909481
[22716]	train's auc: 0.998051	valid's auc: 0.90948
[22717]	train's auc: 0.998051	valid's auc: 0.909479
[22718]	train's auc: 0.998051	valid's auc: 0.909475
[22719]	train's auc: 0.998052	valid's auc: 0.909475
[22720]	train's auc: 0.998052	valid's auc: 0.909476
[22721]	train's auc: 0.998052	valid's auc: 0.909477
[22722]	train's auc: 0.998053	valid's auc: 0.909477
[22723]	train's 

In [ ]:
test = reduce_mem_usage(pd.read_csv('../input/test.csv'))
sub_df = pd.DataFrame({"ID_code":test["ID_code"]})
sub_df['target'] = predictions
sub_df.to_csv("submission.csv", index=False)